# Pre-process LIDC-IDR

In [1]:
import numpy as np
import os
import SimpleITK as sitk
from PIL import Image
import pydicom
import cv2
import nibabel as nib
import pydicom
#用pytracking环境执行
import skimage.io as io
import SimpleITK as sitk
import torch


/home/wangc/anaconda3/envs/test1/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


### Some functions

In [3]:
def loadFile(filename):
    ds = sitk.ReadImage(filename)
    #pydicom.dcmread(filename)
    img_array = sitk.GetArrayFromImage(ds)
    frame_num, width, height = img_array.shape
    #print("frame_num, width, height: "+str((frame_num, width, height)))
    return img_array, frame_num, width, height

'''
def loadFileInformation(filename):
    information = {}
    ds = pydicom.read_file(filename)
    information['PatientID'] = ds.PatientID
    information['PatientName'] = ds.PatientName
    information['PatientSex'] = ds.PatientSex
    information['StudyID'] = ds.StudyID
    information['StudyDate'] = ds.StudyDate
    information['StudyTime'] = ds.StudyTime
    information['Manufacturer'] = ds.Manufacturer
    return information
'''

def get_3d_img_for_one_case(img_path_list, img_format="dcm"):
    img_3d=[]
    for idx, img_path in enumerate(img_path_list):
        print("progress: "+str(idx/len(img_path_list))+"; "+str(img_path), end="\r")
        img_slice, frame_num, _, _ = loadFile(img_path)
        assert frame_num==1
        img_3d.append(img_slice)
    img_3d=np.array(img_3d)
    return img_3d.reshape(img_3d.shape[0], img_3d.shape[2], img_3d.shape[3])

### for all LIDC-IDRI images

In [4]:
# the path to LIDC-IDRI raw images

LIDC_IDRI_raw_path = "/mnt/wangc/LIDC/TCIA_LIDC-IDRI_20200921/LIDC-IDRI"

The file structure should be like this\
\
/data/Airway/LIDC-IDRI\
    /LIDC-IDRI-0001\
        /1.3.6.1.4.1.14519.5.2.1.6279.6001.298806137288633453246975630178\
            /1.3.6.1.4.1.14519.5.2.1.6279.6001.179049373636438705059720603192\
                /1-001.dcm\
                /1-002.dcm\
                ...\
    /LIDC-IDRI-0002\
    ...

In [5]:
LIDC_IDRI_raw_img_dict = {}
img_names = os.listdir(LIDC_IDRI_raw_path)
img_names.sort()
img_names

path_to_a_case = ""

def find_imgs(input_path):
    global path_to_a_case
    items = os.listdir(input_path)
    items.sort()
    #print("There are "+str(items)+" in "+str(input_path))
    All_file_flag = True
    for item in items:
        if os.path.isdir(input_path+"/"+item):
            All_file_flag = False
            break
    if All_file_flag and len(items)>10:
        #print("we get "+str(input_path))
        path_to_a_case = input_path
    else:
        for item in items:
            if os.path.isdir(input_path+"/"+item):
                #print("open filefloder: "+str(input_path+"/"+item))
                find_imgs(input_path+"/"+item)
    
for idx, img_name in enumerate(img_names):
    print(idx/len(img_names), end="\r")
    find_imgs(LIDC_IDRI_raw_path+"/"+img_name)
    slice_names = os.listdir(path_to_a_case)
    slice_names.sort()
    LIDC_IDRI_raw_img_dict[img_name]=[]
    for slice_name in slice_names:
        if slice_name.split(".")[1]=="dcm":
            LIDC_IDRI_raw_img_dict[img_name].append(path_to_a_case+"/"+slice_name)

In [6]:
print("Show the case names: "+str(LIDC_IDRI_raw_img_dict.keys()))

Show the case names: dict_keys(['LIDC-IDRI-0001', 'LIDC-IDRI-0002', 'LIDC-IDRI-0003', 'LIDC-IDRI-0004', 'LIDC-IDRI-0005', 'LIDC-IDRI-0006', 'LIDC-IDRI-0007', 'LIDC-IDRI-0008', 'LIDC-IDRI-0009', 'LIDC-IDRI-0010', 'LIDC-IDRI-0011', 'LIDC-IDRI-0012', 'LIDC-IDRI-0013', 'LIDC-IDRI-0014', 'LIDC-IDRI-0015', 'LIDC-IDRI-0016', 'LIDC-IDRI-0017', 'LIDC-IDRI-0018', 'LIDC-IDRI-0019', 'LIDC-IDRI-0020', 'LIDC-IDRI-0021', 'LIDC-IDRI-0022', 'LIDC-IDRI-0023', 'LIDC-IDRI-0024', 'LIDC-IDRI-0025', 'LIDC-IDRI-0026', 'LIDC-IDRI-0027', 'LIDC-IDRI-0028', 'LIDC-IDRI-0029', 'LIDC-IDRI-0030', 'LIDC-IDRI-0031', 'LIDC-IDRI-0032', 'LIDC-IDRI-0033', 'LIDC-IDRI-0034', 'LIDC-IDRI-0035', 'LIDC-IDRI-0036', 'LIDC-IDRI-0037', 'LIDC-IDRI-0038', 'LIDC-IDRI-0039', 'LIDC-IDRI-0040', 'LIDC-IDRI-0041', 'LIDC-IDRI-0042', 'LIDC-IDRI-0043', 'LIDC-IDRI-0044', 'LIDC-IDRI-0045', 'LIDC-IDRI-0046', 'LIDC-IDRI-0047', 'LIDC-IDRI-0048', 'LIDC-IDRI-0049', 'LIDC-IDRI-0050', 'LIDC-IDRI-0051', 'LIDC-IDRI-0052', 'LIDC-IDRI-0053', 'LIDC-IDRI-005

In [7]:
# set output path

output_image_path = "/mnt/wangc/LIDC/new"

In [8]:
if not os.path.exists(output_image_path):
    os.mkdir(output_image_path)
    
for case in LIDC_IDRI_raw_img_dict.keys():
    img_3d = get_3d_img_for_one_case(LIDC_IDRI_raw_img_dict[case])
    sitk.WriteImage(sitk.GetImageFromArray(img_3d),
                    output_image_path+"/"+case+".nii.gz")

KeyboardInterrupt: 

In [9]:
if not os.path.exists(output_image_path):
    os.mkdir(output_image_path)
    
for case in LIDC_IDRI_raw_img_dict.keys():
    print(output_image_path+"/"+case+".nii.gz")


/mnt/wangc/LIDC/new/LIDC-IDRI-0001.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0002.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0003.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0004.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0005.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0006.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0007.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0008.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0009.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0010.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0011.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0012.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0013.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0014.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0015.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0016.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0017.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0018.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0019.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0020.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0021.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0022.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0023.nii.gz
/mnt/wangc/LIDC/new/LIDC-IDRI-0024

### for the labeled LIDC-IDRI images

In [10]:
LIDC_IDRI_anno_path = "/mnt/wangc/LIDC/TCIA_LIDC-IDRI_20200921/LIDC-IDRI_annotation"

anno_names = os.listdir(LIDC_IDRI_anno_path)
for idx, name in enumerate(anno_names):
    anno_names[idx]=name.split(".nii.gz")[0]
print(anno_names)

['1.3.6.1.4.1.14519.5.2.1.6279.6001.100332161840553388986847034053', '1.3.6.1.4.1.14519.5.2.1.6279.6001.100225287222365663678666836860', '.DS_Store', '1.3.6.1.4.1.14519.5.2.1.6279.6001.100398138793540579077826395208', '1.3.6.1.4.1.14519.5.2.1.6279.6001.110678335949765929063942738609', '1.3.6.1.4.1.14519.5.2.1.6279.6001.100530488926682752765845212286', '1.3.6.1.4.1.14519.5.2.1.6279.6001.111172165674661221381920536987', '1.3.6.1.4.1.14519.5.2.1.6279.6001.114218724025049818743426522343', '1.3.6.1.4.1.14519.5.2.1.6279.6001.114914167428485563471327801935', '1.3.6.1.4.1.14519.5.2.1.6279.6001.113586291551175790743673929831', '1.3.6.1.4.1.14519.5.2.1.6279.6001.115386642382564804180764325545', '1.3.6.1.4.1.14519.5.2.1.6279.6001.116097642684124305074876564522', '1.3.6.1.4.1.14519.5.2.1.6279.6001.116703382344406837243058680403', '1.3.6.1.4.1.14519.5.2.1.6279.6001.119209873306155771318545953948', '1.3.6.1.4.1.14519.5.2.1.6279.6001.119806527488108718706404165837', '1.3.6.1.4.1.14519.5.2.1.6279.6001

In [11]:
LIDC_IDRI_all_raw_img_dict = {}
for case in os.listdir(LIDC_IDRI_raw_path):
    for name_1 in os.listdir(LIDC_IDRI_raw_path+"/"+case):
        for name_2 in os.listdir(LIDC_IDRI_raw_path+"/"+case+"/"+name_1):
            img_names = os.listdir(LIDC_IDRI_raw_path+"/"+case+"/"+name_1+"/"+name_2)
            img_names.sort()
            if len(img_names)>10:
                LIDC_IDRI_all_raw_img_dict[case.split("-")[2]] = []
                for slice_name in img_names:
                    if slice_name.split(".")[1]=="dcm":
                        LIDC_IDRI_all_raw_img_dict[case.split("-")[2]].append(LIDC_IDRI_raw_path+"/"+case+"/"+name_1+"/"+name_2+"/"+slice_name)

In [ ]:
LIDC_IDRI_all_raw_img_dict

In [ ]:
LIDC_IDRI_annotated = {}
LIDC_IDRI_annotation_path = LIDC_IDRI_anno_path

for case in os.listdir(LIDC_IDRI_raw_path):
    for name_1 in os.listdir(LIDC_IDRI_raw_path+"/"+case):
        for name_2 in os.listdir(LIDC_IDRI_raw_path+"/"+case+"/"+name_1):
            if name_2 in anno_names:
                print(LIDC_IDRI_raw_path+"/"+case+"/"+name_1+"/"+name_2)
                img_names = os.listdir(LIDC_IDRI_raw_path+"/"+case+"/"+name_1+"/"+name_2)
                img_names.sort()
                LIDC_IDRI_annotated[case.split("-")[2]] = {}
                LIDC_IDRI_annotated[case.split("-")[2]]["image"] = []
                LIDC_IDRI_annotated[case.split("-")[2]]["label"] = LIDC_IDRI_annotation_path+"/"+name_2+".nii.gz"
                for slice_name in img_names:
                    if slice_name.split(".")[1]=="dcm":
                        LIDC_IDRI_annotated[case.split("-")[2]]["image"].append(LIDC_IDRI_raw_path+"/"+case+"/"+name_1+"/"+name_2+"/"+slice_name)

In [16]:
len(LIDC_IDRI_annotated.keys())

40

In [ ]:
### show the info of dcm
for case in LIDC_IDRI_annotated.keys():
    print(case, end="\n")
    dicom_file = pydicom.dcmread(LIDC_IDRI_annotated[case]["image"][0])
    keys = list(dicom_file.keys())
    for idx, key in enumerate(keys):
        if str(key) == "(0028, 0030)":
            i = idx
            break
    print(dicom_file[list(dicom_file.keys())[i]])
    print("----------")

In [19]:
LIDC_IDRI_annotated

{'0066': {'image': ['/mnt/wangc/LIDC/TCIA_LIDC-IDRI_20200921/LIDC-IDRI/LIDC-IDRI-0066/1.3.6.1.4.1.14519.5.2.1.6279.6001.143774983852765282237869625332/1.3.6.1.4.1.14519.5.2.1.6279.6001.430109407146633213496148200410/1-001.dcm',
   '/mnt/wangc/LIDC/TCIA_LIDC-IDRI_20200921/LIDC-IDRI/LIDC-IDRI-0066/1.3.6.1.4.1.14519.5.2.1.6279.6001.143774983852765282237869625332/1.3.6.1.4.1.14519.5.2.1.6279.6001.430109407146633213496148200410/1-002.dcm',
   '/mnt/wangc/LIDC/TCIA_LIDC-IDRI_20200921/LIDC-IDRI/LIDC-IDRI-0066/1.3.6.1.4.1.14519.5.2.1.6279.6001.143774983852765282237869625332/1.3.6.1.4.1.14519.5.2.1.6279.6001.430109407146633213496148200410/1-003.dcm',
   '/mnt/wangc/LIDC/TCIA_LIDC-IDRI_20200921/LIDC-IDRI/LIDC-IDRI-0066/1.3.6.1.4.1.14519.5.2.1.6279.6001.143774983852765282237869625332/1.3.6.1.4.1.14519.5.2.1.6279.6001.430109407146633213496148200410/1-004.dcm',
   '/mnt/wangc/LIDC/TCIA_LIDC-IDRI_20200921/LIDC-IDRI/LIDC-IDRI-0066/1.3.6.1.4.1.14519.5.2.1.6279.6001.143774983852765282237869625332/1.3.6

Save the images and annotations

In [22]:

output_image_path = "/mnt/wangc/LIDC/image"
output_label_path = "/mnt/wangc/LIDC/label"


if not os.path.exists(output_image_path):
    os.makedirs(output_image_path)

if not os.path.exists(output_label_path):
    os.makedirs(output_label_path)
i=0
for case in LIDC_IDRI_annotated.keys():
    i+=1
    img_3d = get_3d_img_for_one_case(LIDC_IDRI_annotated[case]["image"])
    sitk.WriteImage(sitk.GetImageFromArray(img_3d),
                    output_image_path+"/"+case+".nii.gz")
    img_label_arr, _, _, _ = loadFile(LIDC_IDRI_annotated[case]["label"])
    sitk.WriteImage(sitk.GetImageFromArray(img_label_arr),
                    output_label_path+"/"+case+'.nii.gz')
    print(f'完成{i/40*100}%')

完成2.5%ss: 0.9986357435197817; /mnt/wangc/LIDC/TCIA_LIDC-IDRI_20200921/LIDC-IDRI/LIDC-IDRI-0066/1.3.6.1.4.1.14519.5.2.1.6279.6001.143774983852765282237869625332/1.3.6.1.4.1.14519.5.2.1.6279.6001.430109407146633213496148200410/1-733.dcmmmm
完成5.0%ss: 0.9982993197278912; /mnt/wangc/LIDC/TCIA_LIDC-IDRI_20200921/LIDC-IDRI/LIDC-IDRI-0140/1.3.6.1.4.1.14519.5.2.1.6279.6001.850568285181410483219385441815/1.3.6.1.4.1.14519.5.2.1.6279.6001.139258777898746693365877042411/1-588.dcmmmm
完成7.5%ss: 0.9979338842975206; /mnt/wangc/LIDC/TCIA_LIDC-IDRI_20200921/LIDC-IDRI/LIDC-IDRI-0328/1.3.6.1.4.1.14519.5.2.1.6279.6001.112657410053794387237858900758/1.3.6.1.4.1.14519.5.2.1.6279.6001.156322145453198768801776721493/1-484.dcmmm
完成10.0%s: 0.9982174688057041; /mnt/wangc/LIDC/TCIA_LIDC-IDRI_20200921/LIDC-IDRI/LIDC-IDRI-0376/1.3.6.1.4.1.14519.5.2.1.6279.6001.760852670133552234806401724338/1.3.6.1.4.1.14519.5.2.1.6279.6001.119806527488108718706404165837/1-561.dcmmm
完成12.5%s: 0.9969788519637462; /mnt/wangc/LIDC/TCIA

In [2]:
import os
import numpy as np
import skimage.io as io
import SimpleITK as sitk


# build the raw_data_dict for train

raw_data_dict = dict()

LIDC_IDRI_file_path = "/mnt/wangc/LIDC"
LIDC_IDRI_raw_path = LIDC_IDRI_file_path+"/image"
LIDC_IDRI_label_path = LIDC_IDRI_file_path+"/label"

LIDC_IDRI_raw_names = os.listdir(LIDC_IDRI_raw_path)
LIDC_IDRI_raw_names.sort()

LIDC_IDRI_label_names = os.listdir(LIDC_IDRI_label_path)
LIDC_IDRI_label_names.sort()

case_names = []

for case in LIDC_IDRI_raw_names:
    temp = case.split(".")[0]
    #print(temp)
    case_names.append(temp)
    raw_data_dict["LIDC_IDRI_"+temp]={}
    raw_data_dict["LIDC_IDRI_"+temp]["image"]=LIDC_IDRI_raw_path+"/"+case

for case in LIDC_IDRI_label_names:
    temp = case.split(".")[0]
    temp=temp[:-6]
    # print(temp)
    if temp in case_names:
        raw_data_dict["LIDC_IDRI_"+temp]["label"]=LIDC_IDRI_label_path+"/"+case

LIDC_IDRI_data_dict = raw_data_dict







In [3]:
LIDC_IDRI_data_dict

{'LIDC_IDRI_LIDC_IDRI_0066': {'image': '/mnt/wangc/LIDC/image/LIDC_IDRI_0066.nii.gz',
  'label': '/mnt/wangc/LIDC/label/LIDC_IDRI_0066_label.nii.gz'},
 'LIDC_IDRI_LIDC_IDRI_0140': {'image': '/mnt/wangc/LIDC/image/LIDC_IDRI_0140.nii.gz',
  'label': '/mnt/wangc/LIDC/label/LIDC_IDRI_0140_label.nii.gz'},
 'LIDC_IDRI_LIDC_IDRI_0328': {'image': '/mnt/wangc/LIDC/image/LIDC_IDRI_0328.nii.gz',
  'label': '/mnt/wangc/LIDC/label/LIDC_IDRI_0328_label.nii.gz'},
 'LIDC_IDRI_LIDC_IDRI_0376': {'image': '/mnt/wangc/LIDC/image/LIDC_IDRI_0376.nii.gz',
  'label': '/mnt/wangc/LIDC/label/LIDC_IDRI_0376_label.nii.gz'},
 'LIDC_IDRI_LIDC_IDRI_0403': {'image': '/mnt/wangc/LIDC/image/LIDC_IDRI_0403.nii.gz',
  'label': '/mnt/wangc/LIDC/label/LIDC_IDRI_0403_label.nii.gz'},
 'LIDC_IDRI_LIDC_IDRI_0430': {'image': '/mnt/wangc/LIDC/image/LIDC_IDRI_0430.nii.gz',
  'label': '/mnt/wangc/LIDC/label/LIDC_IDRI_0430_label.nii.gz'},
 'LIDC_IDRI_LIDC_IDRI_0438': {'image': '/mnt/wangc/LIDC/image/LIDC_IDRI_0438.nii.gz',
  'label

In [4]:
def reverse_img_3d_np(img_3d):
    img_3d_shape=img_3d.shape
    reverse_img_3d = np.zeros(img_3d_shape)
    # reverse from the 1st channel
    for i in range(img_3d_shape[0]):
        print("progress: "+str(i/img_3d_shape[0]), end="\r")
        reverse_img_3d[img_3d_shape[0]-i-1,:,:]=img_3d[i,:,:]
    return reverse_img_3d

In [13]:
output_file_path ='/mnt/wangc/LIDC/image2'
for k,v in LIDC_IDRI_data_dict.items():
    case=k
    if int(k[-4:])>1000:
        raw_img = io.imread(v['image'], plugin='simpleitk')
        res_img=reverse_img_3d_np(raw_img)#other img you need to handle(not all image)
        sitk.WriteImage(sitk.GetImageFromArray(res_img),output_file_path+'/'+case+'.nii.gz')